# Script to Process Data Generated from Fixed Bed Testing

Process data from XR unit with 16 fixed bed reactors, labelled as XR

Load libraries and import dataset. The dataset to be analyzed is set by modifying the line Generation = str(x): where x is 1, 2, 3, 4, 5 and 2NC for each of the generations (1-5) and the generation removing the cost as objective (2NC).

In [116]:
# Importing the dataset
import warnings
warnings.filterwarnings("ignore")
import numpy as np
import pandas as pd
# String to be modified to 1, 2, 3, 4, 5 or 2NC
Generation = str("2NC")
data = pd.read_excel("A1_G"+Generation+"_FBTesting_XR16x_RawData.xlsx", sheet_name ='Run Data')
data['FIDF_FileName'].replace('', np.nan, inplace=True)
data.dropna(subset=['FIDF_FileName'], inplace=True)

The flow indicators in the fixed bed reactor unit is converted into the name of the gas, the temperature and pressure are renamed, and the time is converted to time on stream.

In [117]:
#Assign The Corresponding Gas Flow Indicators to The Actual Gases
FIC = data.filter(regex='FIC_1[1-7]0_PV').columns
FIC_gas = ['H2_in_PV', 'He_in_PV', 'N2_in_PV', '40%CO2 in N2_in_PV', 'CH4_in_PV', '5%O2 in N2_in_PV', '10%C3 in N2_in_PV']
data[FIC_gas] = data[FIC]
data["N2_dil_in"] = data["FIC_300_PV"]
#Rename the Temperature and Pressure Column Name
data["Temperature (°C)"] = data["Reactor_Temperature_PV"]
data["Pressure (barg)"] = data["Reactor_Inlet_Pressure"]
#Calculate the time on stream
data['Run Start Time'] = data.groupby('RunName')['UtcTime'].transform('min')
data['Time on Stream'] = data['UtcTime'] - data['Run Start Time']
data['Time on Stream (h)'] = data['Time on Stream'].dt.total_seconds() / 3600

The Gaseous products anaylzed by the GC TCD and FID are renamed.

In [118]:
#Rename the Column Names of the Gas Concentration
FID_cols = [col for col in data.columns if 'FID' in col and 'Conc' in col]
TCD_cols = [col for col in data.columns if 'TCD' in col and 'Conc' in col]
FID_cols = [col for col in data.columns if 'FID' in col and 'Conc' in col]
FID_split = [item.split('_',1)[1] for item in FID_cols]
TCD_cols = [col for col in data.columns if 'TCD' in col and 'Conc' in col]
data[FID_split] = data[FID_cols].copy()
data_2 = data.copy()

FID_cols = [col for col in data.columns if 'FID' in col and 'Conc' in col]
FID_split = [item.split('_',1)[1] for item in FID_cols]
FID_rssplit = [item.rsplit('_',1)[0] for item in FID_split]
TCD_cols = [col for col in data.columns if 'TCD' in col and 'Conc' in col]
TCD_split = [item.rsplit('_',2)[1] for item in TCD_cols]

Sum of the carbon-based species normalized by the number of carbon, the product conversion, and individual product selectivities are calculated.

In [119]:
#Calculate the Sum of carbons
data["Sumcarbon (%)"] = (1*(data["TCD_CO_Conc"]+data["TCD_CO2_Conc"]+data["FIDB_CO_Conc"]+data["FIDF_CH4_Conc"]+data["FIDB_MeOH_Conc"])
+2*(data["FIDB_EtOH_Conc"]+data["FIDF_C2H4_Conc"]+data["FIDF_C2H6_Conc"])
+3*(data["FIDB_1_PrOH_Conc"]+data["FIDB_2_PrOH_Conc"]+data["FIDF_C3H6_Conc"]+data["FIDF_C3H8_Conc"])
+4*(data["FIDB_1_BuOH_Conc"]+data["FIDF_1_C4H8_Conc"]+data["FIDF_i_C4H10_Conc"]+data["FIDF_i_C4H8_Conc"]+
    data["FIDF_n_C4H10_Conc"]+data["FIDF_1_3_C4H6_Conc"]))

#Calculate CO2 conversion
data["CO2 Conversion (%)"]= 100*(data["Sumcarbon (%)"]-data["TCD_CO2_Conc"])/data["Sumcarbon (%)"]

#Calculate individual product selectivities
data['MeOH Selectivity (%)'] = 100*(data["FIDB_MeOH_Conc"]/(data["Sumcarbon (%)"]-data["TCD_CO2_Conc"]))
data['CH4 Selectivity(%)'] = 100*(data["FIDF_CH4_Conc"]/(data["Sumcarbon (%)"]-data["TCD_CO2_Conc"]))
data['CO Selectivity(%)'] = 100*((data["TCD_CO_Conc"]+data["FIDB_CO_Conc"])/(data["Sumcarbon (%)"]-data["TCD_CO2_Conc"]))
data['C2-C4 Selectivity(%)'] = 100*(2*(data["FIDB_EtOH_Conc"]+data["FIDF_C2H4_Conc"]+data["FIDF_C2H6_Conc"])
+3*(data["FIDB_1_PrOH_Conc"]+data["FIDB_2_PrOH_Conc"]+data["FIDF_C3H6_Conc"]+data["FIDF_C3H8_Conc"])
+4*(data["FIDB_1_BuOH_Conc"]+data["FIDF_1_C4H8_Conc"]+data["FIDF_C4H10_Conc"]+data["FIDF_C4H8_Conc"]
+data["FIDF_i_C4H10_Conc"]+data["FIDF_i_C4H8_Conc"]+data["FIDF_n_C4H10_Conc"]+data["FIDF_1_3_C4H6_Conc"]))/(data["Sumcarbon (%)"]-data["TCD_CO2_Conc"])

The inlet gas flowrates are calculated based on the process values. Based on the concentration of the individual gas species, the flowrate of the gases are calculated using helium as an internal standard.

In [120]:
#Calculate the inlet flowrates
data_2 = data.copy()
data['Tot_Gas_Flow'] = data[FIC_gas].sum(axis=1)
data['phi_mix'] = data['Reactor_Gas_Flow_Nml_min'] / (data['Tot_Gas_Flow']/16)
data['CO2_in (ml/min)'] = data['phi_mix']* (0.4*data['40%CO2 in N2_in_PV']/ 16)  
data['N2_in (ml/min)'] =  data["N2_dil_in"]/16+data['phi_mix']* ((0.6*data['40%CO2 in N2_in_PV'] + data['N2_in_PV'])/ 16) 
data['He_in (ml/min)'] =  data['phi_mix']*  (data['He_in_PV'] / 16)
data['H2_in (ml/min)'] = data['phi_mix']*  (data['H2_in_PV'] / 16) 

data['CO2:H2 (3:1) (ml/min)'] =  data['CO2_in (ml/min)']+ data['H2_in (ml/min)']

#Calculate the product flowrates based on gas chromatograms
data['Q_GC'] = data['He_in (ml/min)'] / (data['TCD_He_Conc'] * 0.01)
for rows in data_2[TCD_cols]:
    data_2[rows] = data['Q_GC'] * data[rows] * 0.01

TCD_fr = ['TCD_' + string  + '_fr (ml/min)' for string in TCD_split]
data[TCD_fr] = data_2[TCD_cols]
del data_2

data_2 = data.copy()
for rows in data_2[FID_split]:
    data_2[rows] = data['Q_GC'] * data[rows] * 0.01

FID_fr = [string  + '_fr (ml/min)' for string in FID_rssplit]
data[FID_fr] = data_2[FID_split]
del data_2

data['H2_fr (ml/min)'] =  data['TCD_H2_fr (ml/min)']
data['He_fr (ml/min)'] =  data['TCD_He_fr (ml/min)']
data['N2_fr (ml/min)'] =  data['TCD_N2_fr (ml/min)']
data['CO2_fr (ml/min)'] =  data['TCD_CO2_fr (ml/min)']
data['CO_fr (ml/min)'] = data['CO_fr (ml/min)']+data['TCD_CO_fr (ml/min)']

data["Temperature Set (°C)"] =data["Reactor_Temperature_SP"]
data["Pressure Set (barg)"] = data["ReactorPressure_SP"]

From the processed raw data, specific columns are selected to be exported as mean value and standard deviation.

In [121]:
#Select specific columns to be exported
export = data.copy()
export_str = [
"RunName","Temperature Set (°C)","FIC_110_SP","FIC_120_SP","FIC_130_SP","FIC_140_SP","FIC_150_SP","FIC_160_SP","FIC_170_SP","FIC_300_SP",
"Pressure Set (barg)","Reactor","Block","Temperature (°C)","Pressure (barg)","Time on Stream (h)",

"CO2_in (ml/min)","N2_in (ml/min)","He_in (ml/min)","H2_in (ml/min)","CO2:H2 (3:1) (ml/min)",
"H2_fr (ml/min)","He_fr (ml/min)","N2_fr (ml/min)",

"CO2_fr (ml/min)","CO_fr (ml/min)","CH4_fr (ml/min)","MeOH_fr (ml/min)",
"C2H6_fr (ml/min)","C2H4_fr (ml/min)","EtOH_fr (ml/min)","C3H8_fr (ml/min)","C3H6_fr (ml/min)","1_PrOH_fr (ml/min)","2_PrOH_fr (ml/min)",
"n_C4H10_fr (ml/min)","i_C4H10_fr (ml/min)","1_C4H8_fr (ml/min)","i_C4H8_fr (ml/min)","1_3_C4H6_fr (ml/min)","1_BuOH_fr (ml/min)",

"Sumcarbon (%)","CO2 Conversion (%)","MeOH Selectivity (%)","CH4 Selectivity(%)","CO Selectivity(%)","C2-C4 Selectivity(%)"]

exp_XR = export[export_str]

#Calculate the mean values of multiple injections of the same catalyst under the same condition
mean_df = pd.DataFrame(columns=exp_XR.columns)
exp_XR_mean = exp_XR.groupby(["Reactor","Temperature Set (°C)","FIC_110_SP","FIC_120_SP","FIC_130_SP","FIC_140_SP","FIC_150_SP",
"FIC_160_SP","FIC_170_SP","FIC_300_SP","Pressure Set (barg)"], as_index=False).mean()
exp_XR_mean = exp_XR_mean.drop(["FIC_110_SP","FIC_120_SP","FIC_130_SP","FIC_140_SP","FIC_150_SP",
"FIC_160_SP","FIC_170_SP","FIC_300_SP"], axis=1)
exp_XR_mean['Unit']='XR'
first_column = exp_XR_mean.pop('Unit')
exp_XR_mean.insert(0, 'Unit', first_column)
exp_XR_mean.to_csv('A1_G'+Generation+'_FBData_XR16x_mean.csv', index=False)

#Calculate the standard deviation of multiple injections of the same catalyst under the same condition

std_df = pd.DataFrame(columns=exp_XR.columns)
exp_XR_std = exp_XR.groupby(["Reactor","Temperature Set (°C)","FIC_110_SP","FIC_120_SP","FIC_130_SP","FIC_140_SP","FIC_150_SP",
"FIC_160_SP","FIC_170_SP","FIC_300_SP","Pressure Set (barg)"], as_index=False).std()
exp_XR_std = exp_XR_std.drop(["FIC_110_SP","FIC_120_SP","FIC_130_SP","FIC_140_SP","FIC_150_SP",
"FIC_160_SP","FIC_170_SP","FIC_300_SP"], axis=1)
exp_XR_std['Unit']='XR'
first_column = exp_XR_std.pop('Unit')
exp_XR_std.insert(0, 'Unit', first_column)

CondCount = exp_XR.groupby(["Reactor","Temperature Set (°C)","FIC_110_SP","FIC_120_SP","FIC_130_SP","FIC_140_SP","FIC_150_SP",
"FIC_160_SP","FIC_170_SP","FIC_300_SP","Pressure Set (barg)"], as_index=False).count()
exp_XR_std['Count']=CondCount["Temperature (°C)"]

exp_XR_std.to_csv('A1_G'+Generation+'_FBData_XR16x_std.csv', index=False)


# Script to Process Data Generated from Fixed Bed Testing

Process data from XD unit with 4 fixed bed reactors, labelled as XDB

Load libraries and import dataset. The dataset to be analyzed is set by modifying the line Generation = str(x): where x is 1, 2, 3, 4, 5 and 2NC for each of the generations (1-5) and the generation removing the cost as objective (2NC).

In [122]:
# Importing the dataset
import warnings
warnings.filterwarnings("ignore")
import numpy as np
import pandas as pd
# String to be modified to 1, 2, 3, 4, 5 or 2NC
data = pd.read_excel("A1_G"+Generation+"_FBTesting_XDB4x_RawData.xlsx", sheet_name ='Run Data')
data['FID_F_FileName'].replace('', np.nan, inplace=True)
data.dropna(subset=['FID_F_FileName'], inplace=True)

The flow indicators in the fixed bed reactor unit are converted into the name of the gas, the temperature and pressure are renamed, and the time is converted to time on stream.

In [123]:
#Assign The Corresponding Gas Flow Indicators to The Actual Gases
FIC = data.filter(regex='FIC_1[1-5]0_PV').columns
FIC_gas = ['N2_in_PV', 'He_in_PV', 'H2_in_PV', '40%CO2 in N2_in_PV', 'CH4_in_PV']
data[FIC_gas] = data[FIC]
data["N2_dil_in"] = data["FIC_300_PV"]
#Rename the Temperature and Pressure Column Name
data["Temperature (°C)"] = data["Reactor_Temperature_PV"]
data["Pressure (barg)"] = data["Reactor_Inlet_Pressure"]
#Calculate the time on stream
data['Run Start Time'] = data.groupby('RunName')['UtcTime'].transform('min')
data['Time on Stream'] = data['UtcTime'] - data['Run Start Time']
data['Time on Stream (h)'] = data['Time on Stream'].dt.total_seconds() / 3600

The Gaseous products anaylzed by the GC TCD and FID are renamed.

In [124]:
#Rename the Column Names of the Gas Concentration
TCD_cols = [col for col in data.columns if 'TCD' in col and 'Conc' in col]
TCD_split = [item.rsplit('_',2)[1] for item in TCD_cols]

FID_cols = [col for col in data.columns if 'FID' in col and 'Conc' in col]
FID_split = [item.split('_',1)[1] for item in FID_cols]
FID_ssplit = [item.split('_',1)[1] for item in FID_split]
FID_rssplit = [item.rsplit('_',1)[0] for item in FID_ssplit]

FID_rename = ['FID' + string for string in FID_split]
data[FID_rename] = data[FID_cols].copy()

TCD_rename = ['TCD_' + string +  '_Conc' for string in TCD_split]
data[TCD_rename] = data[TCD_cols].copy()

Sum of the carbon-based species normalized by the number of carbon, the product conversion, and individual product selectivities are calculated.

In [125]:
#Calculate the Sum of carbons
data["Sumcarbon (%)"] = (1*(data["TCD_CO2_Conc"]+data["FIDB_CO_Conc"]+data["FIDF_CH4_Conc"]+data["FIDB_MeOH_Conc"])
+2*(data["FIDB_EtOH_Conc"]+data["FIDF_C2H4_Conc"]+data["FIDF_C2H6_Conc"])
+3*(data["FIDB_1_PrOH_Conc"]+data["FIDB_2_PrOH_Conc"]+data["FIDF_C3H6_Conc"]+data["FIDF_C3H8_Conc"])
+4*(data["FIDB_1_BuOH_Conc"]+data["FIDF_1_C4H8_Conc"]+data["FIDF_i_C4H10_Conc"]+data["FIDF_i_C4H8_Conc"]+
    data["FIDF_n_C4H10_Conc"]+data["FIDF_1_3_C4H6_Conc"]))

#Calculate CO2 conversion
data["CO2 Conversion (%)"]= 100*(data["Sumcarbon (%)"]-data["TCD_CO2_Conc"])/data["Sumcarbon (%)"]

#Calculate individual product selectivities
data['MeOH Selectivity (%)'] = 100*(data["FIDB_MeOH_Conc"]/(data["Sumcarbon (%)"]-data["TCD_CO2_Conc"]))
data['CH4 Selectivity(%)'] = 100*(data["FIDF_CH4_Conc"]/(data["Sumcarbon (%)"]-data["TCD_CO2_Conc"]))
data['CO Selectivity(%)'] = 100*(data["FIDB_CO_Conc"]/(data["Sumcarbon (%)"]-data["TCD_CO2_Conc"]))
data['C2-C4 Selectivity(%)'] = 100*(2*(data["FIDB_EtOH_Conc"]+data["FIDF_C2H4_Conc"]+data["FIDF_C2H6_Conc"])
+3*(data["FIDB_1_PrOH_Conc"]+data["FIDB_2_PrOH_Conc"]+data["FIDF_C3H6_Conc"]+data["FIDF_C3H8_Conc"])
+4*(data["FIDB_1_BuOH_Conc"]+data["FIDF_1_C4H8_Conc"]+data["FIDF_i_C4H10_Conc"]
+data["FIDF_i_C4H8_Conc"]+data["FIDF_n_C4H10_Conc"]+data["FIDF_1_3_C4H6_Conc"]))/(data["Sumcarbon (%)"]-data["TCD_CO2_Conc"])

The inlet gas flowrates are calculated based on the process values. Based on the concentration of the individual gas species, the flowrate of the gases are calculated using helium as an internal standard.

In [126]:
#Calculate the inlet flowrates
data_2 = data.copy()
data['Tot_Gas_Flow'] = data[FIC_gas].sum(axis=1)
data['phi_mix'] = data['Reactor_Gas_Flow_Nml_min'] / (data['Tot_Gas_Flow']/4)
data['CO2_in (ml/min)'] = data['phi_mix']* (0.4*data['40%CO2 in N2_in_PV']/ 4)  
data['N2_in (ml/min)'] =  data["N2_dil_in"]/4+data['phi_mix']* ((0.6*data['40%CO2 in N2_in_PV'] + data['N2_in_PV'])/ 4) 
data['He_in (ml/min)'] =  data['phi_mix']*  (data['He_in_PV'] / 4)
data['H2_in (ml/min)'] = data['phi_mix']*  (data['H2_in_PV'] / 4) 
data['CO2:H2 (3:1) (ml/min)'] =  data['CO2_in (ml/min)']+ data['H2_in (ml/min)']

#Calculate the product flowrates based on gas chromatograms
data['Q_GC'] = data['He_in (ml/min)'] / (data['TCD_He_Conc'] * 0.01)
for rows in data_2[TCD_rename]:
    data_2[rows] = data['Q_GC'] * data[rows] * 0.01

TCD_fr = ['TCD_' + string  + '_fr (ml/min)' for string in TCD_split]
data[TCD_fr] = data_2[TCD_rename]
del data_2

data_2 = data.copy()
for rows in data_2[FID_rename]:
    data_2[rows] = data['Q_GC'] * data[rows] * 0.01

FID_fr = [string  + '_fr (ml/min)' for string in FID_rssplit]
data[FID_fr] = data_2[FID_rename]
del data_2

data['H2_fr (ml/min)'] =  data['TCD_H2_fr (ml/min)']
data['He_fr (ml/min)'] =  data['TCD_He_fr (ml/min)']
data['N2_fr (ml/min)'] =  data['TCD_N2_fr (ml/min)']
data['CO2_fr (ml/min)'] =  data['TCD_CO2_fr (ml/min)']

data["Temperature Set (°C)"] = data["Reactor_Temperature_SP"]
data["Pressure Set (barg)"] = data["RPC_Setpoint_SP"]

From the processed raw data, specific columns are selected to be exported as mean value and standard deviation.

In [127]:
#Select specific columns to be exported
export = data.copy()
export_str = [
"RunName","Temperature Set (°C)","FIC_110_SP","FIC_120_SP","FIC_130_SP","FIC_140_SP","FIC_150_SP","FIC_300_SP",
"Pressure Set (barg)","Reactor","Block","Temperature (°C)","Pressure (barg)","Time on Stream (h)",

"CO2_in (ml/min)","N2_in (ml/min)","He_in (ml/min)","H2_in (ml/min)","CO2:H2 (3:1) (ml/min)",
"H2_fr (ml/min)","He_fr (ml/min)","N2_fr (ml/min)",

"CO2_fr (ml/min)","CO_fr (ml/min)","CH4_fr (ml/min)","MeOH_fr (ml/min)",
"C2H6_fr (ml/min)","C2H4_fr (ml/min)","EtOH_fr (ml/min)","C3H8_fr (ml/min)","C3H6_fr (ml/min)","1_PrOH_fr (ml/min)","2_PrOH_fr (ml/min)",
"n_C4H10_fr (ml/min)","i_C4H10_fr (ml/min)","1_C4H8_fr (ml/min)","i_C4H8_fr (ml/min)","1_3_C4H6_fr (ml/min)","1_BuOH_fr (ml/min)",

"Sumcarbon (%)","CO2 Conversion (%)","MeOH Selectivity (%)","CH4 Selectivity(%)","CO Selectivity(%)","C2-C4 Selectivity(%)"]

exp_XDB = export[export_str]

#Calculate the mean values of multiple injections of the same catalyst under the same condition
mean_df = pd.DataFrame(columns=exp_XDB.columns)
exp_XDB_mean = exp_XDB.groupby(["Reactor","Temperature Set (°C)","FIC_110_SP","FIC_120_SP","FIC_130_SP","FIC_140_SP","FIC_150_SP","FIC_300_SP","Pressure Set (barg)"], as_index=False).mean()
exp_XDB_mean = exp_XDB_mean.drop(["FIC_110_SP","FIC_120_SP","FIC_130_SP","FIC_140_SP","FIC_150_SP","FIC_300_SP"], axis=1)
exp_XDB_mean['Unit']='XD B'
first_column = exp_XDB_mean.pop('Unit')
exp_XDB_mean.insert(0, 'Unit', first_column)
exp_XDB_mean.to_csv('A1_G'+Generation+'_FBData_XDB4x_mean.csv', index=False)

#Calculate the standard deviation of multiple injections of the same catalyst under the same condition
std_df = pd.DataFrame(columns=exp_XDB.columns)
exp_XDB_std = exp_XDB.groupby(["Reactor","Temperature Set (°C)","FIC_110_SP","FIC_120_SP","FIC_130_SP","FIC_140_SP","FIC_150_SP","FIC_300_SP","Pressure Set (barg)"], as_index=False).std()
exp_XDB_std = exp_XDB_std.drop(["FIC_110_SP","FIC_120_SP","FIC_130_SP","FIC_140_SP","FIC_150_SP","FIC_300_SP"], axis=1)
exp_XDB_std['Unit']='XD B'
first_column = exp_XDB_std.pop('Unit')
exp_XDB_std.insert(0, 'Unit', first_column)

CondCount = exp_XDB.groupby(["Reactor","Temperature Set (°C)","FIC_110_SP","FIC_120_SP","FIC_130_SP","FIC_140_SP","FIC_150_SP","FIC_300_SP","Pressure Set (barg)"], as_index=False).count()
exp_XDB_std['Count']=CondCount["Temperature (°C)"]

exp_XDB_mean.to_csv('A1_G'+Generation+'_FBData_XDB4x_std.csv', index=False)


# Script to Process Data Generated from Fixed Bed Testing

Process data from XD unit with 4 fixed bed reactors, labelled as XDC


Load libraries and import dataset. The dataset to be analyzed is set by modifying the line Generation = str(x): where x is 1, 2, 3, 4, 5 and 2NC for each of the generations (1-5) and the generation removing the cost as objective (2NC).

In [128]:
# Importing the dataset
import warnings
warnings.filterwarnings("ignore")
import numpy as np
import pandas as pd
# String to be modified to 1, 2, 3, 4, 5 or 2NC

data = pd.read_excel("A1_G"+Generation+"_FBTesting_XDC4x_RawData.xlsx", sheet_name ='Run Data')
data['FID_F_FileName'].replace('', np.nan, inplace=True)
data.dropna(subset=['FID_F_FileName'], inplace=True)

The flow indicators in the fixed bed reactor unit are converted into the name of the gas, the temperature and pressure are renamed, and the time is converted to time on stream.

In [129]:
#Assign The Corresponding Gas Flow Indicators to The Actual Gases
FIC = data.filter(regex='FIC_1[1-5]0_PV').columns
FIC_gas = ['N2_in_PV', 'He_in_PV', 'H2_in_PV', '40%CO2 in N2_in_PV', 'CH4_in_PV']
data[FIC_gas] = data[FIC]
data["N2_dil_in"] = data["FIC_300_PV"]
#Rename the Temperature and Pressure Column Name
data["Temperature (°C)"] = data["Reactor_Temperature_PV"]
data["Pressure (barg)"] = data["Reactor_Inlet_Pressure"]
#Calculate the time on stream
data['Run Start Time'] = data.groupby('RunName')['UtcTime'].transform('min')
data['Time on Stream'] = data['UtcTime'] - data['Run Start Time']
data['Time on Stream (h)'] = data['Time on Stream'].dt.total_seconds() / 3600

The Gaseous products anaylzed by the GC TCD and FID are renamed.

In [130]:
#Rename the Column Names of the Gases.
TCD_cols = [col for col in data.columns if 'TCD' in col and 'Conc' in col]
TCD_split = [item.rsplit('_',2)[1] for item in TCD_cols]

FID_cols = [col for col in data.columns if 'FID' in col and 'Conc' in col]
FID_split = [item.split('_',1)[1] for item in FID_cols]
FID_ssplit = [item.split('_',1)[1] for item in FID_split]
FID_rssplit = [item.rsplit('_',1)[0] for item in FID_ssplit]

FID_rename = ['FID' + string for string in FID_split]
data[FID_rename] = data[FID_cols].copy()

TCD_rename = ['TCD_' + string +  '_Conc' for string in TCD_split]
data[TCD_rename] = data[TCD_cols].copy()

Sum of the carbon-based species normalized by the number of carbon, the product conversion, and individual product selectivities are calculated.

In [131]:
#Calculate the Sum of carbons
data["Sumcarbon (%)"] = (1*(data["TCD_CO2_Conc"]+data["FIDB_CO_Conc"]+data["FIDF_CH4_Conc"]+data["FIDB_MeOH_Conc"])
+2*(data["FIDB_EtOH_Conc"]+data["FIDF_C2H4_Conc"]+data["FIDF_C2H6_Conc"])
+3*(data["FIDB_1_PrOH_Conc"]+data["FIDB_2_PrOH_Conc"]+data["FIDF_C3H6_Conc"]+data["FIDF_C3H8_Conc"])
+4*(data["FIDB_1_BuOH_Conc"]+data["FIDF_1_C4H8_Conc"]+data["FIDF_i_C4H10_Conc"]+data["FIDF_i_C4H8_Conc"]+
    data["FIDF_n_C4H10_Conc"]+data["FIDF_1_3_C4H6_Conc"]))

#Calculate CO2 conversion
data["CO2 Conversion (%)"]= 100*(data["Sumcarbon (%)"]-data["TCD_CO2_Conc"])/data["Sumcarbon (%)"]

#Calculate individual product selectivities
data['MeOH Selectivity (%)'] = 100*(data["FIDB_MeOH_Conc"]/(data["Sumcarbon (%)"]-data["TCD_CO2_Conc"]))
data['CH4 Selectivity(%)'] = 100*(data["FIDF_CH4_Conc"]/(data["Sumcarbon (%)"]-data["TCD_CO2_Conc"]))
data['CO Selectivity(%)'] = 100*(data["FIDB_CO_Conc"]/(data["Sumcarbon (%)"]-data["TCD_CO2_Conc"]))
data['C2-C4 Selectivity(%)'] = 100*(2*(data["FIDB_EtOH_Conc"]+data["FIDF_C2H4_Conc"]+data["FIDF_C2H6_Conc"])
+3*(data["FIDB_1_PrOH_Conc"]+data["FIDB_2_PrOH_Conc"]+data["FIDF_C3H6_Conc"]+data["FIDF_C3H8_Conc"])
+4*(data["FIDB_1_BuOH_Conc"]+data["FIDF_1_C4H8_Conc"]+data["FIDF_C4H10_Conc"]+data["FIDF_C4H8_Conc"]
+data["FIDF_i_C4H10_Conc"]+data["FIDF_i_C4H8_Conc"]+data["FIDF_n_C4H10_Conc"]+data["FIDF_1_3_C4H6_Conc"]))/(data["Sumcarbon (%)"]-data["TCD_CO2_Conc"])

The inlet gas flowrates are calculated based on the process values. Based on the concentration of the individual gas species, the flowrate of the gases are calculated using helium as an internal standard.

In [132]:
#Calculate the inlet flowrates
data_2 = data.copy()
data['Tot_Gas_Flow'] = data[FIC_gas].sum(axis=1)
data['phi_mix'] = data['Reactor_Gas_Flow_Nml_min'] / (data['Tot_Gas_Flow']/4)
data['CO2_in (ml/min)'] = data['phi_mix']* (0.4*data['40%CO2 in N2_in_PV']/ 4)  
data['N2_in (ml/min)'] =  data["N2_dil_in"]/4+data['phi_mix']* ((0.6*data['40%CO2 in N2_in_PV'] + data['N2_in_PV'])/ 4) 
data['He_in (ml/min)'] =  data['phi_mix']*  (data['He_in_PV'] / 4)
data['H2_in (ml/min)'] = data['phi_mix']*  (data['H2_in_PV'] / 4) 
data['CO2:H2 (3:1) (ml/min)'] =  data['CO2_in (ml/min)']+ data['H2_in (ml/min)']

#Calculate the product flowrates based on gas chromatograms
data['Q_GC'] = data['He_in (ml/min)'] / (data['TCD_He_Conc'] * 0.01)
for rows in data_2[TCD_rename]:
    data_2[rows] = data['Q_GC'] * data[rows] * 0.01

TCD_fr = ['TCD_' + string  + '_fr (ml/min)' for string in TCD_split]
data[TCD_fr] = data_2[TCD_rename]
del data_2

data_2 = data.copy()
for rows in data_2[FID_rename]:
    data_2[rows] = data['Q_GC'] * data[rows] * 0.01

FID_fr = [string  + '_fr (ml/min)' for string in FID_rssplit]
data[FID_fr] = data_2[FID_rename]
del data_2

data['H2_fr (ml/min)'] =  data['TCD_H2_fr (ml/min)']
data['He_fr (ml/min)'] =  data['TCD_He_fr (ml/min)']
data['N2_fr (ml/min)'] =  data['TCD_N2_fr (ml/min)']
data['CO2_fr (ml/min)'] =  data['TCD_CO2_fr (ml/min)']

data["Temperature Set (°C)"] = data["Reactor_Temperature_SP"]
data["Pressure Set (barg)"] = data["RPC_Setpoint_SP"]

From the processed raw data, specific columns are selected to be exported as mean value and standard deviation.

In [133]:
#Select specific columns to be exported
export = data.copy()
export_str = [
"RunName","Temperature Set (°C)","FIC_110_SP","FIC_120_SP","FIC_130_SP","FIC_140_SP","FIC_150_SP","FIC_300_SP",
"Pressure Set (barg)","Reactor","Block","Temperature (°C)","Pressure (barg)","Time on Stream (h)",

"CO2_in (ml/min)","N2_in (ml/min)","He_in (ml/min)","H2_in (ml/min)","CO2:H2 (3:1) (ml/min)",
"H2_fr (ml/min)","He_fr (ml/min)","N2_fr (ml/min)",

"CO2_fr (ml/min)","CO_fr (ml/min)","CH4_fr (ml/min)","MeOH_fr (ml/min)",
"C2H6_fr (ml/min)","C2H4_fr (ml/min)","EtOH_fr (ml/min)","C3H8_fr (ml/min)","C3H6_fr (ml/min)","1_PrOH_fr (ml/min)","2_PrOH_fr (ml/min)",
"n_C4H10_fr (ml/min)","i_C4H10_fr (ml/min)","1_C4H8_fr (ml/min)","i_C4H8_fr (ml/min)","1_3_C4H6_fr (ml/min)","1_BuOH_fr (ml/min)",

"Sumcarbon (%)","CO2 Conversion (%)","MeOH Selectivity (%)","CH4 Selectivity(%)","CO Selectivity(%)","C2-C4 Selectivity(%)"]

exp_XDC = export[export_str]

#Calculate the mean values of multiple injections of the same catalyst under the same condition
mean_df = pd.DataFrame(columns=exp_XDC.columns)
exp_XDC_mean = exp_XDC.groupby(["Reactor","Temperature Set (°C)","FIC_110_SP","FIC_120_SP","FIC_130_SP","FIC_140_SP","FIC_150_SP","FIC_300_SP","Pressure Set (barg)"], as_index=False).mean()
exp_XDC_mean = exp_XDC_mean.drop(["FIC_110_SP","FIC_120_SP","FIC_130_SP","FIC_140_SP","FIC_150_SP","FIC_300_SP"], axis=1)
exp_XDC_mean['Unit']='XD C'
first_column = exp_XDC_mean.pop('Unit')
exp_XDC_mean.insert(0, 'Unit', first_column)
exp_XDC_mean.to_csv('A1_G'+Generation+'_FBData_XDC4x_mean.csv', index=False)

#Calculate the standard deviation of multiple injections of the same catalyst under the same condition
std_df = pd.DataFrame(columns=exp_XDC.columns)
exp_XDC_std = exp_XDC.groupby(["Reactor","Temperature Set (°C)","FIC_110_SP","FIC_120_SP","FIC_130_SP","FIC_140_SP","FIC_150_SP","FIC_300_SP","Pressure Set (barg)"], as_index=False).std()
exp_XDC_std = exp_XDC_std.drop(["FIC_110_SP","FIC_120_SP","FIC_130_SP","FIC_140_SP","FIC_150_SP","FIC_300_SP"], axis=1)
exp_XDC_std['Unit']='XD C'
first_column = exp_XDC_std.pop('Unit')
exp_XDC_std.insert(0, 'Unit', first_column)

CondCount = exp_XDC.groupby(["Reactor","Temperature Set (°C)","FIC_110_SP","FIC_120_SP","FIC_130_SP","FIC_140_SP","FIC_150_SP","FIC_300_SP","Pressure Set (barg)"], as_index=False).count()
exp_XDC_std['Count']=CondCount["Temperature (°C)"]

exp_XDC_std.to_csv('A1_G'+Generation+'_FBData_XDC4x_std.csv', index=False)


# Script to Merge Data from Different Fixed Bed Reactors


In [134]:
# Merge data from Avantium Units as mean values
import numpy as np
import pandas as pd


data_A = pd.read_csv('A1_G'+Generation+'_FBData_XR16x_mean.csv')
data_B = pd.read_csv('A1_G'+Generation+'_FBData_XDB4x_mean.csv')
data_C = pd.read_csv('A1_G'+Generation+'_FBData_XDC4x_mean.csv')

data = pd.concat([data_A, data_B, data_C], axis=0, ignore_index=True)
data.to_csv('A1_G'+Generation+'_FBData_AllUnits_mean.csv', index=False)

# Merge data from Avantium Units as standard deviation
data_A = pd.read_csv('A1_G'+Generation+'_FBData_XR16x_std.csv')
data_B = pd.read_csv('A1_G'+Generation+'_FBData_XDB4x_std.csv')
data_C = pd.read_csv('A1_G'+Generation+'_FBData_XDC4x_std.csv')

data = pd.concat([data_A, data_B, data_C], axis=0, ignore_index=True)
data.to_csv('A1_G'+Generation+'_FBData_AllUnits_std.csv', index=False)

# Script to Merge Synthesis, Solid Dispense and Catalysis Data per Generation
Read all the raw and processed files, and merge them.

In [135]:
import numpy as np
import pandas as pd


#Read files
data_A = pd.read_csv('A1_G'+Generation+'_CombVialPrep.csv')
data_B = pd.read_csv('A1_G'+Generation+'_SolidDispense.csv')
data_C = pd.read_csv('A1_G'+Generation+'_ImpregnationDetails.csv')
data_D = pd.read_csv('A1_G'+Generation+'_ImpregnationBarcode.csv')
data_E = pd.read_csv('A1_G'+Generation+'_CatalystDispenseBarcode.csv')
data_F = pd.read_csv('A1_G'+Generation+'_FBReactorLoading.csv')
data_G = pd.read_csv('A1_G'+Generation+'_FBData_AllUnits_mean.csv')
data_H = pd.read_csv('A1_G'+Generation+'_Cost.csv')

#Add new columns
data_G['Unit Reactor'] = data_G["Unit"]+ " " + data_G["Reactor"].map(str)
data_G = data_G.drop(["Unit","Reactor"], axis=1)
data_F['Unit Reactor'] = data_F["Unit"]+ " " + data_F["Reactor"].map(str)
data_F = data_F.drop(["Unit","Reactor"], axis=1)

#Merge data on common columns
data = pd.merge(data_A, data_C, left_on='Combinational Vial Number', right_on='Combinational Vial Number', how='left')
data = pd.merge(data, data_B, left_on='Impregnation Vial Number', right_on='Impregnation Vial Number', how='left')
data = pd.merge(data, data_D, left_on='Impregnation Vial Number', right_on='Impregnation Vial Number', how='left')
data = pd.merge(data, data_E, left_on='Impregnation Vial Number Barcode', right_on='Impregnation Vial Number Barcode', how='left')
data = pd.merge(data, data_F, left_on='Catalysis Vial Number Barcode', right_on='Catalysis Vial Number Barcode', how='left')
data = pd.merge(data, data_H, left_on='Impregnation Vial Number Barcode', right_on='Impregnation Vial Number Barcode', how='left')
data = pd.merge(data, data_G, left_on='Unit Reactor', right_on='Unit Reactor', how='left')

Calculate the liquid volume that was dispensed for the synthesis and which support was used.

In [136]:
#Obtain volumes of metal salt solution dispensed
Dispensed = [col for col in data.columns if 'Dispensed [mL]' in col]
Dispensed.remove('Water Dispensed [mL]')
Dispensed_no_Water = Dispensed
Dispensed = [col for col in data.columns if 'Dispensed [mL]' in col]
Solid_Dispense = [col for col in data.columns if ' Actual [mg]' in col]

#Find the support that was dispensed
Support_ID = data[Solid_Dispense].idxmax(axis=1)
Support_ID = Support_ID.str.split(expand=True)[0]
Support_ID = Support_ID.replace("Zirconia", "ZrO2")
Support_ID = Support_ID.replace("Titania", "TiO2")
Support_ID = Support_ID.replace("Alumina", "Al2O3")
Support_ID = Support_ID.replace("Silica", "SiO2")
data["Support"] = Support_ID

Calculate the nominal metal loading and the formation rate of the gases quantified by GC

In [137]:
Mass_Metal=(0.2*data[Dispensed_no_Water].sum(axis=1)*data["ActualAmount [mL]"]/data[Dispensed].sum(axis=1))
Tot_Mass=(0.2*data[Dispensed_no_Water].sum(axis=1)*data["ActualAmount [mL]"]/data[Dispensed].sum(axis=1)+0.001*data[Solid_Dispense].max(axis=1))

data["Total Metal Loading [wt%]"]  = 100*Mass_Metal/Tot_Mass
for rows in data[Dispensed_no_Water]:
    Mass_Atom=(0.2*data[rows]*data["ActualAmount [mL]"]/data[Dispensed].sum(axis=1))
    data[rows.split(' ',1)[0] + " Loading [wt%]"] = 100*Mass_Atom/Tot_Mass

FlowRates = [col for col in data.columns if 'fr (ml/min)' in col]

for rows in FlowRates:
        data[rows.rsplit('_',1)[0]+ " Formation Rate [mol/(h*gMetal)]"]=(data[rows]*60*100000*0.000001/(8.314*273.15))/(0.05*0.01*data["Total Metal Loading [wt%]"])



Export the data

In [138]:
data.to_csv('A1_G'+Generation+'_AllDataProcessed.csv', index=False)